# IMPORT LIBRARIES

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
import json # library to handle JSON files
!pip install geocoder
import geocoder

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

print("Libraries imported.")
print('Libraries imported.')

    100% |████████████████████████████████| 102kB 15.5MB/s 
Libraries imported.
Libraries imported.


# Download Dataset of New York City Neighbourhoods with their lattitude and longitude

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

#### Use geopy library to get the latitude and longitude values of New York City.

In [4]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7308619, -73.9871558.


#### Create a map of New York with neighborhoods superimposed on top.

In [5]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

### Setting Up Foursquare Credentials

In [6]:
# The code was removed by Watson Studio for sharing.

#### Now, let's get the top 100 venues that are in every neighbourhood within a radius of 500 meters.

In [ ]:
radius = 500
LIMIT = 200

venues = []

for lat, long, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()['response']['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [8]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(10243, 7)


Neighborhood   Latitude  Longitude         VenueName  VenueLatitude  \
0    Wakefield  40.894705 -73.847201  Lollipops Gelato      40.894123   
1    Wakefield  40.894705 -73.847201          Rite Aid      40.896521   
2    Wakefield  40.894705 -73.847201  Carvel Ice Cream      40.890487   
3    Wakefield  40.894705 -73.847201     Dunkin Donuts      40.890631   
4    Wakefield  40.894705 -73.847201            SUBWAY      40.890656   

   VenueLongitude   VenueCategory  
0      -73.845892    Dessert Shop  
1      -73.844680        Pharmacy  
2      -73.848568  Ice Cream Shop  
3      -73.849027      Donut Shop  
4      -73.849192  Sandwich Place

In [9]:
venuesvenues_df['VenueCategory']

array(['Dessert Shop', 'Pharmacy', 'Ice Cream Shop', 'Donut Shop',
       'Sandwich Place', 'Food Truck', 'Pizza Place', 'Laundromat',
       'Discount Store', 'Mattress Store', 'Grocery Store', 'Restaurant',
       'Bus Station', 'Baseball Field', 'Chinese Restaurant',
       'Fried Chicken Joint', 'Liquor Store', 'Salon / Barbershop',
       'Fast Food Restaurant', 'Gift Shop', 'Park',
       'Caribbean Restaurant', 'Diner', 'Seafood Restaurant',
       'Deli / Bodega', 'Bowling Alley', 'Bus Stop', 'Platform',
       'Convenience Store', 'Juice Bar', 'Metro Station', 'Bakery',
       'Cosmetics Shop', 'Plaza', 'Music Venue', 'River', 'Playground',
       'Bank', 'Home Service', 'Gym', 'Gourmet Shop',
       'Latin American Restaurant', 'Pub', 'Beer Bar', 'Burger Joint',
       'Mexican Restaurant', 'Bar', 'Coffee Shop', 'Warehouse Store',
       'Wings Joint', 'Thrift / Vintage Store', 'Spanish Restaurant',
       'Supermarket', 'Trail', 'Rental Car Location', 'Candy Store',
       '

#### From the above categories we get to know that there are three categories named "Indian Restaurant", "North Indian Restaurant","South Indian Restaurant"

### Analyze each Neighborhood

In [202]:
ny_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

print(ny_onehot.shape)
ny_onehot.head()

(10243, 427)


Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Wakefield                  0               0                  0   
1     Wakefield                  0               0                  0   
2     Wakefield                  0               0                  0   
3     Wakefield                  0               0                  0   
4     Wakefield                  0               0                  0   

   African Restaurant  Airport Tram  American Restaurant  Animal Shelter  \
0                   0             0                    0               0   
1                   0             0                    0               0   
2                   0             0                    0               0   
3                   0             0                    0               0   
4                   0             0                    0               0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0                    0              0                0          0           0   
1                    0              0                0          0           0   
2                    0              0                0          0           0   
3                    0              0                0          0           0   
4                    0              0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                 0           0      0          0                0         0   
1                 0           0      0          0                0         0   
2                 0           0      0          0                0         0   
3                 0           0      0          0                0         0   
4                 0           0      0          0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  \
0            0           0                   0              0   
1            0           0                   0              0   
2            0           0                   0              0   
3            0           0                   0              0   
4            0           0                   0              0   

   

**Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category**

In [237]:
ny_grouped = ny_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(ny_grouped.shape)
ny_grouped

(301, 427)


Neighborhoods  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.000000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.000000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.020408            0.00   
13                  Baychester           0.000000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.000000            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.000000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.000000            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57             

### Create a new dataframe containing mean occurence of Indian Restaurant, South Indian Restaurant, North Indian Restaurant

In [238]:
ny_indian_rest = ny_grouped[["Neighborhoods","Indian Restaurant"]]
ny_indian_rest.head()

Neighborhoods  Indian Restaurant
0       Allerton                0.0
1       Annadale                0.0
2  Arden Heights                0.0
3      Arlington                0.0
4       Arrochar                0.0

In [239]:
ny_indian_rest.rename(columns={"Neighborhoods":"Neighborhood"},inplace=True)

In [240]:
ny_indian_rest

Neighborhood  Indian Restaurant
0                     Allerton           0.000000
1                     Annadale           0.000000
2                Arden Heights           0.000000
3                    Arlington           0.000000
4                     Arrochar           0.000000
5                      Arverne           0.000000
6                      Astoria           0.020000
7              Astoria Heights           0.000000
8                   Auburndale           0.000000
9                   Bath Beach           0.000000
10           Battery Park City           0.010000
11                   Bay Ridge           0.011111
12                 Bay Terrace           0.000000
13                  Baychester           0.000000
14                     Bayside           0.040541
15                   Bayswater           0.000000
16                Bedford Park           0.000000
17          Bedford Stuyvesant           0.000000
18                  Beechhurst           0.000000
19                    Bellaire           0.000000
20                Belle Harbor           0.000000
21                   Bellerose           0.000000
22                     Belmont           0.000000
23                 Bensonhurst           0.000000
24                Bergen Beach           0.000000
25                  Blissville           0.000000
26                  Bloomfield           0.000000
27                 Boerum Hill           0.012048
28                Borough Park           0.000000
29                Breezy Point           0.000000
30                   Briarwood           0.071429
31              Brighton Beach           0.000000
32               Broad Channel           0.000000
33           Broadway Junction           0.000000
34                   Bronxdale           0.000000
35            Brooklyn Heights           0.020000
36                  Brookville           0.000000
37                 Brownsville           0.000000
38                  Bulls Head           0.000000
39                    Bushwick           0.013514
40                Butler Manor           0.000000
41             Cambria Heights           0.000000
42                    Canarsie           0.000000
43               Carnegie Hill           0.010000
44             Carroll Gardens           0.000000
45                 Castle Hill           0.000000
46           Castleton Corners           0.000000
47              Central Harlem           0.000000
48                  Charleston           0.000000
49                     Chelsea           0.009615
50                   Chinatown           0.000000
51                 City Island           0.000000
52                   City Line           0.000000
53                Civic Center           0.010000
54           Claremont Village           0.000000
55                Clason Point           0.000000
56                     Clifton           0.000000
57                     Clinton           0.000000
58                Clinton Hill           0.030928
59                  Co-op City           0.000000
60                 Cobble Hill           0.010000
61               College Point           0.000000
62                     Concord           0.000000
63                   Concourse           0.000000
64           Concourse Village           0.027778
65                Coney Island           0.000000
66                      Corona           0.000000
67                Country Club           0.000000
68               Crown Heights           0.000000
69               Cypress Hills           0.000000
70                 Ditmas Park           0.000000
71                Dongan Hills           0.000000
72                  Douglaston           0.000000
73                    Downtown           0.000000
74                       Dumbo           0.000000
75               Dyker Heights           0.000000
76               East Elmhurst           0.000000
77               East Flatbush           0.000000
78                 East Harlem           0.000000
79               E

## NOW WE NEED TO FIND AREAS THAT ARE IN CLOSE PROXIMITY TO HIGH RENT ZONES WHILE BEING LOCATED IN LOW RENT ZONE SO THAT IT HAS BOTH ADVANTAGES OF ATTRACTING THE TOURIST AS WELL AS PAYING LOW RENT

In [14]:
rent=pd.read_csv("Neighborhood_Zri_AllHomesPlusMultifamily_Summary.csv")
rent.head()

Date         RegionName State                           Metro  \
0  2018-12-31   Northeast Dallas    TX     Dallas-Fort Worth-Arlington   
1  2018-12-31           Maryvale    AZ         Phoenix-Mesa-Scottsdale   
2  2018-12-31    Upper West Side    NY     New York-Newark-Jersey City   
3  2018-12-31  South Los Angeles    CA  Los Angeles-Long Beach-Anaheim   
4  2018-12-31    Upper East Side    NY     New York-Newark-Jersey City   

               County         City  SizeRank   Zri       MoM       QoQ  \
0       Dallas County       Dallas         0  1789  0.022286  0.043149   
1     Maricopa County      Phoenix         1  1179  0.015504  0.030594   
2     New York County     New York         2  3826  0.028218  0.055157   
3  Los Angeles County  Los Angeles         3  2506  0.014164  0.027049   
4     New York County     New York         4  3500  0.009227  0.016260   

        YoY  ZriRecordCnt  
0 -0.007765         57050  
1  0.067935         49156  
2 -0.001044         71051  
3  0.036394         34570  
4 -0.001427         82606

In [15]:
rent_ny=rent[rent["City"]=="New York"]
rent_ny.head()

Date          RegionName State                        Metro  \
2   2018-12-31     Upper West Side    NY  New York-Newark-Jersey City   
4   2018-12-31     Upper East Side    NY  New York-Newark-Jersey City   
7   2018-12-31       East New York    NY  New York-Newark-Jersey City   
9   2018-12-31  Washington Heights    NY  New York-Newark-Jersey City   
11  2018-12-31             Astoria    NY  New York-Newark-Jersey City   

             County      City  SizeRank   Zri       MoM       QoQ       YoY  \
2   New York County  New York         2  3826  0.028218  0.055157 -0.001044   
4   New York County  New York         4  3500  0.009227  0.016260 -0.001427   
7      Kings County  New York         7  2218  0.009558  0.018365 -0.000451   
9   New York County  New York         9  2538  0.011155  0.024213 -0.046940   
11    Queens County  New York        11  2245  0.001785  0.003576 -0.008392   

    ZriRecordCnt  
2          71051  
4          82606  
7          20236  
9          14868  
11         26547

In [16]:
rent_ny=rent_ny[["RegionName","County","Zri"]]
rent_ny.rename(columns={"RegionName":"Neighborhood","County":"County","Zri":"Rent"},inplace=True)
rent_ny.head()

Neighborhood           County  Rent
2      Upper West Side  New York County  3826
4      Upper East Side  New York County  3500
7        East New York     Kings County  2218
9   Washington Heights  New York County  2538
11             Astoria    Queens County  2245

### Find the top 5 neighborhoods with the highest rate index

In [25]:
rent_ny=rent_ny.sort_values(by="Rent",ascending=False)
rent_ny.head()


Neighborhood           County  Rent
589         Tribeca  New York County  7404
1306           SoHo  New York County  5636
2592           NoHo  New York County  4561
842   Carnegie Hill  New York County  4483
493    West Village  New York County  4299

(30, 3)

#### USING GOOGLE DISTANCE MATRIX API FIND THE DISTANCE BETWEEN EACH NEIGHBORHOOD RELATIVE TO THE ABOVE MENTIONED NEIGHBORHOODS

In [61]:
rent_ny_near=rent_ny[rent_ny["County"]=="New York County"]
x = rent_ny_near["Neighborhood"].to_string(header=False,
                  index=False).split("\n")
vals = ['+'.join(ele.split()) for ele in x]
dest="|".join(vals[0:5])
ori="|".join(vals[5:30])
print(dest)
print(ori)
print(rent_ny_near)



Tribeca|SoHo|NoHo|Carnegie+Hill|West+Village
Flatiron+District|Little+Italy|Chelsea|Greenwich+Village|Midtown|East+Village|Sutton+Place|Upper+West+Side|Battery+Park|Lower+East+Side|Financial+District|Tudor+City|Gramercy|Turtle+Bay|Murray+Hill|Upper+East+Side|Garment+District|Roosevelt+Island|Morningside+Heights|Brooklyn+Heights|Hamilton+Heights|Harlem|East+Harlem|Washington+Heights|Inwood
             Neighborhood           County  Rent
589               Tribeca  New York County  7404
1306                 SoHo  New York County  5636
2592                 NoHo  New York County  4561
842         Carnegie Hill  New York County  4483
493          West Village  New York County  4299
413     Flatiron District  New York County  4286
1521         Little Italy  New York County  4239
186               Chelsea  New York County  4211
197     Greenwich Village  New York County  4184
731               Midtown  New York County  4142
99           East Village  New York County  3920
538          Sutton 

##### After setting up API ENTER THE BELOW LINKS WITH YOUR API KEY TO GENERATE JSON CONTAINING DISTANCE MATRIX
##### https://maps.googleapis.com/maps/api/distancematrix/json?origins=Flatiron+District|Little+Italy|Chelsea+NY|Greenwich+Village|Midtown+NY|East+Village|Sutton+Place|Upper+West+Side|Battery+Park|Lower+East+Side|Financial+District|Tudor+City|Gramercy|Turtle+Bay+Manhattan|Murray+Hill|Upper+East+Side|Garment+District|Roosevelt+Island|Morningside+Heights|Brooklyn+Heights&destinations=Tribeca|SoHo|NoHo|Carnegie+Hill|West+Village&mode=bicycling&language=en&key=YourAPIKEY
##### https://maps.googleapis.com/maps/api/distancematrix/json?origins=Hamilton+Heights|Harlem|East+Harlem|Washington+Heights|Inwood&destinations=Tribeca|SoHo|NoHo|Carnegie+Hill|West+Village&mode=bicycling&language=en&key=YourAPIKEY

In [110]:
dist=[]
with open('nyc_1.json') as json_data:
    nyc1_data = json.load(json_data)
distance_data = nyc1_data['rows']
for data in distance_data:
    for x in data['elements']:
        dist.append(x['distance']['text'])
dist
dist1=dist[0:5]
dist2=dist[5:10]
dist3=dist[10:15]
dist4=dist[15:20]
dist5=dist[20:25]
dist6=dist[25:30]
dist7=dist[30:35]
dist8=dist[35:40]
dist9=dist[40:45]
dist10=dist[45:50]
dist11=dist[50:55]
dist12=dist[55:60]
dist13=dist[60:65]
dist14=dist[65:70]
dist15=dist[70:75]
dist16=dist[75:80]
dist17=dist[80:85]
dist18=dist[85:90]
dist19=dist[90:95]
dist20=dist[95:100]
dist21=[]
with open('nyc_2.json') as json_data:
    nyc2_data = json.load(json_data)
distance_data = nyc2_data['rows']
for data in distance_data:
    for x in data['elements']:
        dist21.append(x['distance']['text'])

dist22=dist21[0:5]
dist23=  [5:10]
dist24=dist21[10:15]
dist25=dist21[15:20]
dist26=dist21[20:25]


['3.7 km', '4.5 km', '5.4 km', '13.0 km', '6.6 km']
['20.9 km', '20.4 km', '20.8 km', '10.8 km', '19.2 km']


##### LETS CREATE A DATAFRAME WITH THE NEIGHBORHOOD DISTANCE

In [152]:
dist_df=pd.DataFrame(columns=['DistTribeca','DistSo','DistNo','DistCarHil','DistWestVil'],index=np.arange(25))
c=0
for i in range(20):
    dist_df.iloc[i]=dist[c:c+5]
    c=c+5
d=0
for i in range(20,25):
    dist_df.iloc[i]=dist21[d:d+5]
    d=d+5
dist_df

DistTribeca   DistSo   DistNo DistCarHil DistWestVil
0       3.6 km   2.6 km   1.9 km     7.9 km      1.8 km
1       1.6 km   0.8 km   1.2 km     9.6 km      2.7 km
2       4.4 km   3.0 km   3.1 km     7.1 km      1.5 km
3       2.5 km   1.5 km   1.1 km     8.4 km      0.3 km
4       7.4 km   4.6 km   4.0 km     4.7 km      4.0 km
5       3.6 km   2.7 km   1.6 km     8.0 km      2.3 km
6       9.7 km   8.8 km   7.7 km     2.5 km      8.4 km
7       9.9 km   9.5 km   8.6 km     4.6 km      7.0 km
8       2.1 km   3.0 km   4.8 km    14.1 km      4.8 km
9       2.7 km   2.6 km   2.3 km    10.3 km      3.9 km
10      1.6 km   2.2 km   3.6 km    12.9 km      4.2 km
11      5.6 km   4.8 km   3.6 km     5.8 km      4.3 km
12      4.1 km   3.1 km   2.1 km     7.3 km      2.3 km
13      6.7 km   5.8 km   4.7 km     4.5 km      5.4 km
14      5.5 km   4.6 km   3.5 km     5.7 km      4.1 km
15     12.0 km   9.3 km   8.2 km     2.4 km      8.0 km
16      6.0 km   4.6 km   4.8 km     5.6 km      3.1 km
17     12.5 km  11.7 km  10.5 km     8.8 km     11.2 km
18     12.3 km  11.9 km  12.3 km     4.1 km     10.6 km
19      3.7 km   4.5 km   5.4 km    13.0 km      6.6 km
20     14.5 km  14.0 km  14.4 km     5.7 km     12.8 km
21     14.6 km  14.2 km  12.2 km     3.8 km     10.6 km
22     15.1 km  12.2 km  11.1 km     2.7 km     10.8 km
23     16.6 km  16.2 km  16.5 km     7.4 km     14.9 km
24     20.9 km  20.4 km  20.8 km    10.8 km     19.2 km

In [188]:
dist_df.index=rent_ny[rent_ny["County"]=="New York County"]["Neighborhood"][5:30]
dist_df.rename(columns={"Neighborhood":"Rent"},inplace=True)
rent=rent_ny[rent_ny["County"]=="New York County"]["Rent"][5:30]
rent.index=np.arange(25)

dist_df.reset_index(level=0, inplace=True)
dist_df["Re"]=rent


Neighborhood DistTribeca   DistSo   DistNo DistCarHil DistWestVil  \
0     Flatiron District      3.6 km   2.6 km   1.9 km     7.9 km      1.8 km   
1          Little Italy      1.6 km   0.8 km   1.2 km     9.6 km      2.7 km   
2               Chelsea      4.4 km   3.0 km   3.1 km     7.1 km      1.5 km   
3     Greenwich Village      2.5 km   1.5 km   1.1 km     8.4 km      0.3 km   
4               Midtown      7.4 km   4.6 km   4.0 km     4.7 km      4.0 km   
5          East Village      3.6 km   2.7 km   1.6 km     8.0 km      2.3 km   
6          Sutton Place      9.7 km   8.8 km   7.7 km     2.5 km      8.4 km   
7       Upper West Side      9.9 km   9.5 km   8.6 km     4.6 km      7.0 km   
8          Battery Park      2.1 km   3.0 km   4.8 km    14.1 km      4.8 km   
9       Lower East Side      2.7 km   2.6 km   2.3 km    10.3 km      3.9 km   
10   Financial District      1.6 km   2.2 km   3.6 km    12.9 km      4.2 km   
11           Tudor City      5.6 km   4.8 km   3.6 km     5.8 km      4.3 km   
12             Gramercy      4.1 km   3.1 km   2.1 km     7.3 km      2.3 km   
13           Turtle Bay      6.7 km   5.8 km   4.7 km     4.5 km      5.4 km   
14          Murray Hill      5.5 km   4.6 km   3.5 km     5.7 km      4.1 km   
15      Upper East Side     12.0 km   9.3 km   8.2 km     2.4 km      8.0 km   
16     Garment District      6.0 km   4.6 km   4.8 km     5.6 km      3.1 km   
17     Roosevelt Island     12.5 km  11.7 km  10.5 km     8.8 km     11.2 km   
18  Morningside Heights     12.3 km  11.9 km  12.3 km     4.1 km     10.6 km   
19     Brooklyn Heights      3.7 km   4.5 km   5.4 km    13.0 km      6.6 km   
20     Hamilton Heights     14.5 km  14.0 km  14.4 km     5.7 km     12.8 km   
21               Harlem     14.6 km  14.2 km  12.2 km     3.8 km     10.6 km   
22          East Harlem     15.1 km  12.2 km  11.1 km     2.7 km     10.8 km   
23   Washington Heights     16.6 km  16.2 km  16.5 km     7.4 km     14.9 km   
24               Inwood     20.9 km  20.4 km  20.8 km    10.8 km     19.2 km   

      Re  
0   4286  
1   4239  
2   4211  
3   4184  
4   4142  
5   3920  
6   3843  
7   3826  
8   3825  
9   3814  
10  3798  
11  3757  
12  3732  
13  3656  
14  3621  
15  3500  
16  3492  
17  3269  
18  3171  
19  2949  
20  2929  
21  2879  
22  2869  
23  2538  
24  2355

### After Careful Observation by checking the quantiles the 85 percentile rent stands at 4000. Hence we will exclude other places with rent higher than this

In [191]:
dist_rent_ny=dist_df[dist_df["Re"]<4000].copy()
dist_rent_ny.drop("Rent",1)


Neighborhood DistTribeca   DistSo   DistNo DistCarHil DistWestVil  \
5          East Village      3.6 km   2.7 km   1.6 km     8.0 km      2.3 km   
6          Sutton Place      9.7 km   8.8 km   7.7 km     2.5 km      8.4 km   
7       Upper West Side      9.9 km   9.5 km   8.6 km     4.6 km      7.0 km   
8          Battery Park      2.1 km   3.0 km   4.8 km    14.1 km      4.8 km   
9       Lower East Side      2.7 km   2.6 km   2.3 km    10.3 km      3.9 km   
10   Financial District      1.6 km   2.2 km   3.6 km    12.9 km      4.2 km   
11           Tudor City      5.6 km   4.8 km   3.6 km     5.8 km      4.3 km   
12             Gramercy      4.1 km   3.1 km   2.1 km     7.3 km      2.3 km   
13           Turtle Bay      6.7 km   5.8 km   4.7 km     4.5 km      5.4 km   
14          Murray Hill      5.5 km   4.6 km   3.5 km     5.7 km      4.1 km   
15      Upper East Side     12.0 km   9.3 km   8.2 km     2.4 km      8.0 km   
16     Garment District      6.0 km   4.6 km   4.8 km     5.6 km      3.1 km   
17     Roosevelt Island     12.5 km  11.7 km  10.5 km     8.8 km     11.2 km   
18  Morningside Heights     12.3 km  11.9 km  12.3 km     4.1 km     10.6 km   
19     Brooklyn Heights      3.7 km   4.5 km   5.4 km    13.0 km      6.6 km   
20     Hamilton Heights     14.5 km  14.0 km  14.4 km     5.7 km     12.8 km   
21               Harlem     14.6 km  14.2 km  12.2 km     3.8 km     10.6 km   
22          East Harlem     15.1 km  12.2 km  11.1 km     2.7 km     10.8 km   
23   Washington Heights     16.6 km  16.2 km  16.5 km     7.4 km     14.9 km   
24               Inwood     20.9 km  20.4 km  20.8 km    10.8 km     19.2 km   

      Re  
5   3920  
6   3843  
7   3826  
8   3825  
9   3814  
10  3798  
11  3757  
12  3732  
13  3656  
14  3621  
15  3500  
16  3492  
17  3269  
18  3171  
19  2949  
20  2929  
21  2879  
22  2869  
23  2538  
24  2355

### Now remove neighborhoods that do not lie within 5km of the above mentioned neighborhoods

#### From the above observation we will remove the following neighborhoods due to their low proximity to high rental neighborhood
1. Roosevelt Island
2. Hamilton Heights
3. Washington Heights
4. Inwood

In [199]:
dist_rent_ny.drop([17,20,23,24],inplace=True)
dist_rent_ny

Neighborhood DistTribeca   DistSo   DistNo DistCarHil DistWestVil  \
5          East Village      3.6 km   2.7 km   1.6 km     8.0 km      2.3 km   
6          Sutton Place      9.7 km   8.8 km   7.7 km     2.5 km      8.4 km   
7       Upper West Side      9.9 km   9.5 km   8.6 km     4.6 km      7.0 km   
8          Battery Park      2.1 km   3.0 km   4.8 km    14.1 km      4.8 km   
9       Lower East Side      2.7 km   2.6 km   2.3 km    10.3 km      3.9 km   
10   Financial District      1.6 km   2.2 km   3.6 km    12.9 km      4.2 km   
11           Tudor City      5.6 km   4.8 km   3.6 km     5.8 km      4.3 km   
12             Gramercy      4.1 km   3.1 km   2.1 km     7.3 km      2.3 km   
13           Turtle Bay      6.7 km   5.8 km   4.7 km     4.5 km      5.4 km   
14          Murray Hill      5.5 km   4.6 km   3.5 km     5.7 km      4.1 km   
15      Upper East Side     12.0 km   9.3 km   8.2 km     2.4 km      8.0 km   
16     Garment District      6.0 km   4.6 km   4.8 km     5.6 km      3.1 km   
18  Morningside Heights     12.3 km  11.9 km  12.3 km     4.1 km     10.6 km   
19     Brooklyn Heights      3.7 km   4.5 km   5.4 km    13.0 km      6.6 km   
21               Harlem     14.6 km  14.2 km  12.2 km     3.8 km     10.6 km   
22          East Harlem     15.1 km  12.2 km  11.1 km     2.7 km     10.8 km   

      Re  
5   3920  
6   3843  
7   3826  
8   3825  
9   3814  
10  3798  
11  3757  
12  3732  
13  3656  
14  3621  
15  3500  
16  3492  
18  3171  
19  2949  
21  2879  
22  2869

### BEFORE PERFORMING CLUSTERING WE WILL CLUB RENT AND THE NUMBER OF INDIAN RESTAURANTS IN EACH NEIGHBORHOOD 

In [241]:
z=dist_rent_ny[["Neighborhood","Re"]]
z.loc[z["Neighborhood"] == 'Battery Park', "Neighborhood"] = "Battery Park City"
z.loc[z["Neighborhood"] == 'Harlem', "Neighborhood"] = "Central Harlem"

merged=pd.merge(z, ny_indian_rest, on='Neighborhood', how='inner')

Neighborhood    Re  Indian Restaurant
0          East Village  3920           0.000000
1          Sutton Place  3843           0.040000
2       Upper West Side  3826           0.030000
3     Battery Park City  3825           0.010000
4       Lower East Side  3814           0.000000
5    Financial District  3798           0.010000
6            Tudor City  3757           0.000000
7              Gramercy  3732           0.000000
8            Turtle Bay  3656           0.030000
9           Murray Hill  3621           0.000000
10      Upper East Side  3500           0.000000
11  Morningside Heights  3171           0.023256
12     Brooklyn Heights  2949           0.020000
13       Central Harlem  2879           0.000000
14          East Harlem  2869           0.000000

##### Scaling the data before performing k means

In [244]:
cols = list(merged.columns)
cols.remove('Neighborhood')
merged[cols]


# now iterate over the remaining columns and create a new zscore column
for col in cols:
    col_zscore = col + '_zscore'
    merged[col_zscore] = (merged[col] - merged[col].mean())/merged[col].std(ddof=0)

In [245]:
merged

Neighborhood    Re  Indian Restaurant  Re_zscore  \
0          East Village  3920           0.000000   1.024912   
1          Sutton Place  3843           0.040000   0.815023   
2       Upper West Side  3826           0.030000   0.768684   
3     Battery Park City  3825           0.010000   0.765958   
4       Lower East Side  3814           0.000000   0.735974   
5    Financial District  3798           0.010000   0.692360   
6            Tudor City  3757           0.000000   0.580602   
7              Gramercy  3732           0.000000   0.512456   
8            Turtle Bay  3656           0.030000   0.305293   
9           Murray Hill  3621           0.000000   0.209889   
10      Upper East Side  3500           0.000000  -0.119936   
11  Morningside Heights  3171           0.023256  -1.016734   
12     Brooklyn Heights  2949           0.020000  -1.621868   
13       Central Harlem  2879           0.000000  -1.812676   
14          East Harlem  2869           0.000000  -1.839934   

    Indian Restaurant_zscore  
0                  -0.801777  
1                   2.144926  
2                   1.408250  
3                  -0.065102  
4                  -0.801777  
5                  -0.065102  
6                  -0.801777  
7                  -0.801777  
8                   1.408250  
9                  -0.801777  
10                 -0.801777  
11                  0.911422  
12                  0.671574  
13                 -0.801777  
14                 -0.801777

### Performing Kmeans Clustering

In [248]:
kclusters = 3

manhattan_grouped_clustering = merged.drop(['Neighborhood','Re','Indian Restaurant'], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 
ny_merged = merged.copy()

# add clustering labels
ny_merged["Cluster Labels"] = kmeans.labels_




In [250]:
ny_merged.head()
nymerged=pd.merge(ny_merged, neighborhoods[["Neighborhood","Latitude","Longitude"]], on='Neighborhood', how='inner')

print(nymerged.shape)
nymerged.head()

(16, 8)


Neighborhood    Re  Indian Restaurant  Re_zscore  \
0       East Village  3920               0.00   1.024912   
1       Sutton Place  3843               0.04   0.815023   
2    Upper West Side  3826               0.03   0.768684   
3  Battery Park City  3825               0.01   0.765958   
4    Lower East Side  3814               0.00   0.735974   

   Indian Restaurant_zscore  Cluster Labels   Latitude  Longitude  
0                 -0.801777               1  40.727847 -73.982226  
1                  2.144926               2  40.760280 -73.963556  
2                  1.408250               2  40.787658 -73.977059  
3                 -0.065102               1  40.711932 -74.016869  
4                 -0.801777               1  40.717807 -73.980890

### Lets visualize the resulting cluster

In [251]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nymerged['Latitude'], nymerged['Longitude'], nymerged['Neighborhood'], nymerged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Cluster 1

In [252]:
nymerged.loc[nymerged['Cluster Labels'] == 1]

Neighborhood    Re  Indian Restaurant  Re_zscore  \
0         East Village  3920               0.00   1.024912   
3    Battery Park City  3825               0.01   0.765958   
4      Lower East Side  3814               0.00   0.735974   
5   Financial District  3798               0.01   0.692360   
6           Tudor City  3757               0.00   0.580602   
7             Gramercy  3732               0.00   0.512456   
9          Murray Hill  3621               0.00   0.209889   
10         Murray Hill  3621               0.00   0.209889   
11     Upper East Side  3500               0.00  -0.119936   

    Indian Restaurant_zscore  Cluster Labels   Latitude  Longitude  
0                  -0.801777               1  40.727847 -73.982226  
3                  -0.065102               1  40.711932 -74.016869  
4                  -0.801777               1  40.717807 -73.980890  
5                  -0.065102               1  40.707107 -74.010665  
6                  -0.801777               1  40.746917 -73.971219  
7                  -0.801777               1  40.737210 -73.981376  
9                  -0.801777               1  40.748303 -73.978332  
10                 -0.801777               1  40.764126 -73.812763  
11                 -0.801777               1  40.775639 -73.960508

### Cluster 2

In [253]:
nymerged.loc[nymerged['Cluster Labels'] == 0]

Neighborhood    Re  Indian Restaurant  Re_zscore  \
12  Morningside Heights  3171           0.023256  -1.016734   
13     Brooklyn Heights  2949           0.020000  -1.621868   
14       Central Harlem  2879           0.000000  -1.812676   
15          East Harlem  2869           0.000000  -1.839934   

    Indian Restaurant_zscore  Cluster Labels   Latitude  Longitude  
12                  0.911422               0  40.808000 -73.963896  
13                  0.671574               0  40.695864 -73.993782  
14                 -0.801777               0  40.815976 -73.943211  
15                 -0.801777               0  40.792249 -73.944182

### Cluster 3

In [254]:
nymerged.loc[nymerged['Cluster Labels'] == 2]

Neighborhood    Re  Indian Restaurant  Re_zscore  \
1     Sutton Place  3843               0.04   0.815023   
2  Upper West Side  3826               0.03   0.768684   
8       Turtle Bay  3656               0.03   0.305293   

   Indian Restaurant_zscore  Cluster Labels   Latitude  Longitude  
1                  2.144926               2  40.760280 -73.963556  
2                  1.408250               2  40.787658 -73.977059  
8                  1.408250               2  40.752042 -73.967708